# Führen Sie in einem Jupyter Notebook die folgenden Aufgaben durch:

>Laden Sie die Datei lshw.xml.
>Lesen Sie sich die Datei durch, um den Aufbau kennenzulernen. Geben Sie dazu diese im Notebook aus.
Beantworten Sie die folgenden Fragen mittels der Verwendung von XPath:
- Wie groß ist der Systemspeicher?
- Wie heißt der Prozessor, der im Einsatz ist?
- Welche IO-Ports verwendet die IDE-Schnittstelle?
- Wie heißt das Gerät, das die Fähigkeit für Audio CD playback mitbringt?
- Unter welchen handles sind die Geräte zu finden, die mit einem Icon disc dargestellt werden?

In [17]:
from lxml import etree
from pathlib import Path

path = Path("lshw.xml")

tree = etree.parse(str(path), etree.XMLParser(recover=True))


In [18]:
with open(path, "r") as f:
    print(f.read())

<?xml version="1.0" standalone="yes"?>
<!-- generated by lshw- -->
<!-- GCC 10.2.1 20210110 -->
<!-- Linux 5.10.0-8-amd64 #1 SMP Debian 5.10.46-5 (2021-09-23) x86_64 -->
<!-- GNU libc 2 (glibc 2.31) -->
<list>
  <node id="bs1-lab" claimed="true" class="system" handle="DMI:0001">
    <description>Computer</description>
    <product>VirtualBox</product>
    <vendor>innotek GmbH</vendor>
    <version>1.2</version>
    <serial>0</serial>
    <width units="bits">64</width>
    <configuration>
      <setting id="family" value="Virtual Machine" />
      <setting id="uuid" value="708059AA-BCB9-1145-A9CA-EBD2D2DA0177" />
    </configuration>
    <capabilities>
      <capability id="smbios-2.5">SMBIOS version 2.5</capability>
      <capability id="dmi-2.5">DMI version 2.5</capability>
      <capability id="vsyscall32">32-bit processes</capability>
    </capabilities>
    <node id="core" claimed="true" class="bus" handle="DMI:0008">
      <description>Motherboard</description>
      <product>Virt

In [19]:
# --------------------------------------------------
# Systemeigenschaften
# --------------------------------------------------
mem_size_bytes = int(
    tree.xpath("//node[@class='memory'][description='System memory']/size/text()")[0]
)
mem_size_gib = mem_size_bytes / 2**30

processor_name = tree.xpath("//node[@class='processor']/product/text()")[0]

io_ports_ide = tree.xpath(
    "//node[@id='ide']//resources/resource[@type='ioport']/@value"
)

device_audio_node = tree.xpath("//capability[@id='audio']/ancestor::node[1]")[0]
device_audio_name = (
    device_audio_node.xpath("description/text()")
    or device_audio_node.xpath("product/text()")
)[0]
device_audio_handle = device_audio_node.get("handle")

disc_handles = [
    node.get("handle")
    for node in tree.xpath("//hint[@name='icon'][@value='disc']/ancestor::node[1]")
    if node.get("handle")
]

In [20]:
# --------------------------------------------------
# Ergebnisse
# --------------------------------------------------
print(f"Systemspeicher: {mem_size_gib:.2f} GiB")
print(f"Prozessor:      {processor_name}")
print(f"IDE-IO-Ports:   {', '.join(io_ports_ide)}")
print(f"Audio-Gerät:    {device_audio_name} (Handle: {device_audio_handle})")
print("Handles mit Icon 'disc':")
for h in disc_handles:
    print(" •", h)


Systemspeicher: 4.00 GiB
Prozessor:      Intel(R) Core(TM) i5-8365U CPU @ 1.60GHz
IDE-IO-Ports:   1f0(size=8), 3f6, 170(size=8), 376, d000(size=16)
Audio-Gerät:    DVD reader (Handle: SCSI:02:00:00:00)
Handles mit Icon 'disc':
 • PCI:0000:00:01.1
 • PCI:0000:00:0d.0
 • SCSI:01:00:00:00
